In [1]:
import keras
from keras import applications
from keras.preprocessing.image import ImageDataGenerator
from keras import optimizers
from keras.models import Sequential, Model 
from keras.layers import Dropout, Flatten, Dense, GlobalAveragePooling2D
from keras import backend as k 
from keras.callbacks import CSVLogger, ModelCheckpoint, LearningRateScheduler, TensorBoard, EarlyStopping
from keras import optimizers
from keras.preprocessing.image import ImageDataGenerator, array_to_img, img_to_array, load_img
from keras.utils.vis_utils import plot_model
from keras.applications.mobilenet_v2 import decode_predictions
from keras.layers.normalization import BatchNormalization

from keras.models import Sequential
from keras.layers import Conv2D, MaxPooling2D
from keras.layers import Activation, Dropout, Flatten, Dense

import matplotlib.image as mpimg
import matplotlib.pyplot as plt
import numpy as np
import os

import tensorflow
from time import time

import pandas

import pickle as pk

from keras.wrappers.scikit_learn import KerasClassifier

import numpy as np

seed = 7

Using TensorFlow backend.


## Evaluate Batch size with RMSprop.
#### First, evaluate each size independently (restart kernel each time without clearing output).
#### Then, to the, all sequential to get approximation of the weights really fast and improve accuracy sequentially

In [6]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 14501250146846722254
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 11280557671
locality {
  bus_id: 1
  links {
  }
}
incarnation: 5402522241606931334
physical_device_desc: "device: 0, name: Tesla K80, pci bus id: 0000:00:1e.0, compute capability: 3.7"
]


In [7]:
dir(keras.applications.mobilenet_v2)

['MobileNetV2',
 '__builtins__',
 '__cached__',
 '__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__spec__',
 'absolute_import',
 'decode_predictions',
 'division',
 'keras_modules_injection',
 'mobilenet_v2',
 'preprocess_input',
 'print_function']

In [8]:
np.random.seed(seed)

In [9]:
data_dir = '/data/oxford102/train'
train_data_dir = "/data/oxford102/train/"
validation_data_dir = "/data/oxford102/train/"
img_width, img_height = 256, 256
# batch_size = 32
epochs = 100
nr_categories = 102
nb_train_samples = 4604
nb_validation_samples = 1094 

In [10]:
# train_val_datagen = ImageDataGenerator(preprocessing_function=input_processor, 
#                                            validation_split=0.2)

# train_val_datagen_aug = ImageDataGenerator(
#         #rescale=1. / 255,
#         rotation_range=40,
#         width_shift_range=0.2,
#         height_shift_range=0.2,
#         shear_range=0.2,
#         zoom_range=0.2,
#         horizontal_flip=True,
#         fill_mode='nearest',
#         preprocessing_function=input_processor,
#         validation_split=0.2)

In [11]:
def get_image_generator(input_processor, img_aug=False):
    if not img_aug:
        train_val_datagen = ImageDataGenerator(preprocessing_function=input_processor, 
                                           validation_split=0.2)
    else: 
        train_val_datagen = ImageDataGenerator(
            rotation_range=40,
            width_shift_range=0.2,
            height_shift_range=0.2,
            shear_range=0.2,
            zoom_range=0.2,
            horizontal_flip=True,
            fill_mode='nearest',
            preprocessing_function=input_processor,
            validation_split=0.2)
        
    return train_val_datagen

In [12]:
def get_generators(batch_size, image_size, input_processor, img_aug=False):

    img_width, img_height = image_size
    
    train_val_datagen = get_image_generator(input_processor, img_aug)

    train_generator = train_val_datagen.flow_from_directory(
            train_data_dir,  # this is the target directory
            target_size=(img_width, img_height),  # all images will be resized to 250x250
            batch_size=batch_size,
            subset="training",
            class_mode='categorical')

    validation_generator = train_val_datagen.flow_from_directory(
            train_data_dir,  # this is the target directory
            target_size=(img_width, img_height),  # all images will be resized to 250x250
            subset="validation",
            batch_size=batch_size,
            class_mode='categorical')
    
    return train_generator, validation_generator


In [13]:
#from keras import regularizers

def get_model(network_name="inception_resnet_v2", image_size=(256, 256), verbose=True):
    k.set_learning_phase(0)

    img_width, img_height = image_size
    if network_name == "vgg16":
        base_model = keras.applications.vgg16.VGG16(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.vgg16.preprocess_input
    elif network_name == "vgg19":
        base_model = keras.applications.vgg19.VGG19(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.vgg19.preprocess_input
    elif network_name == "inception_resnet_v2":
        base_model = keras.applications.inception_resnet_v2.InceptionResNetV2(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.inception_resnet_v2.preprocess_input
    elif network_name == "mobilenet_v2":
        base_model = keras.applications.mobilenet_v2.MobileNetV2(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.mobilenet_v2.preprocess_input
    else:
        raise Exception("check your network name")

    for layer in base_model.layers[:]:
        layer.trainable = False

        #Adding custom Layers 
    k.set_learning_phase(1)
    x = base_model.output
    x = Flatten()(x)
    x = Dense(1024, activation="relu", 
              #kernel_regularizer=regularizers.l2(0.01),
             #       activity_regularizer=regularizers.l1(0.001)
             )(x)
    x = Dropout(0.5)(x)
    x = BatchNormalization()(x, training=True)
    #x = Dense(102, activation="relu")(x)
    predictions = Dense(nr_categories, activation="softmax")(x)

    _model = Model(input = base_model.input, output = predictions)
    if verbose:
        _model.summary()
    return _model, input_processor

In [14]:
# _model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001, rho=0.9, epsilon=None, decay=0.0), metrics=["accuracy"])


# With data augmentation

In [20]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    
def train_my_model(train_generator, val_generator, params, _model):
    model_name = "mobilenet_v2"
    num_train_img = 4604
    num_val_img = 1094
#     params = {'network_name': model_name,
#              'image_aug': True,
#              'optimizer': 'SGD',
#              'optimizer_params': None, 
#              'batch_size': 128,
#              'epochs': 100,
#              'image_size': (256, 256),
#              'log_time': None}


    np.random.seed(seed)
    log_time = time()
    params['log_time'] = log_time
    batch_size = params.get("batch_size")

    print(params["optimizer"])
    _model.compile(loss = "categorical_crossentropy", optimizer = params["optimizer"], metrics=["accuracy"])


    base = '/data/oxford102/experiments'
    path = os.path.join(base, str(log_time))
    checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
    tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
    csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

    try:
        if not os.path.exists(path):
            os.makedirs(path)
        history_callback = _model.fit_generator(
                train_generator,
                steps_per_epoch=num_train_img // batch_size,
                epochs=params['epochs'],
                validation_data=validation_generator,
                validation_steps=num_val_img // params['batch_size'],
                callbacks = [checkpoint, early, tensorboard, csv_logger])
    except Exception as e:
        raise(e)
    finally:
        pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
        _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
        print(params)
        params

    return _model, history_callback

# Without data augmentation

In [12]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': True,
         'optimizer': 'SGD',
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.SGD(lr=0.001, momentum=0.9), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
35/35 [==============================] - 29s 841ms/step - loss: 4.1591 - acc: 0.1473 - val_loss: 3.5489 - val_acc: 0.1992

Epoch 00001: val_acc improved from -inf to 0.19922, saving model to /data/oxford102/experiments/1544921965.6249993/mobilenet_v2_1544921965.6249993.h5
Epoch 2/100
35/35 [==============================] - 23s 654ms/step - loss: 3.1554 - acc: 0.2786 - val_loss: 2.9939 - val_acc: 0.2734

Epoch 00002: val_acc improved from 0.19922 to 0.27344, saving model to /data/oxford102/experiments/1544921965.6249993/mobilenet_v2_1544921965.6249993.h5
Epoch 3/100
35/35 [==============================] - 23s 656ms/step - loss: 2.7947 - acc: 0.3366 - val_loss: 2.5649 - val_acc: 0.3867

Epoch 00003: val_acc improved from 0.27344 to 0.38672, saving model to /data/oxford102/experiments/1544921965.6249993/mobilenet_v2_1544921965.6249993.h5
Epoch 4/100
35/35 [==============================] - 23s 652ms/step - loss: 2.5564 - acc: 0.3964 - val_loss: 2.4116 - val_acc: 0.4219

Epoc

In [ ]:
# Hyperparameter optimization

In [ ]:
optimizers

In [ ]:
optimizers.SGD(lr=0.01, decay=1e-6, momentum=0.9, nesterov=True)

In [ ]:
optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False)

In [ ]:
optimizers.RMSprop(lr=0.001, rho=0.9, epsilon=None, decay=0.0)

In [ ]:
optimizers.Adagrad(lr=0.01, epsilon=None, decay=0.0)

In [ ]:
optimizers.Adadelta(lr=1.0, rho=0.95, epsilon=None, decay=0.0)

In [ ]:
optimizers.Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)

In [ ]:
optimizers.Adamax(lr=0.002, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0)

In [ ]:
optimizers.Nadam(lr=0.002, beta_1=0.9, beta_2=0.999, epsilon=None, schedule_decay=0.004)

In [13]:
import talos as ta

In [ ]:
p = {'lr': (0.001, 0.01, 0.1),
     'batch_size': (128),
     'epochs': [150],
     'dropout': (0, 0.5, 5),
     'weight_regulizer':[None],
     'emb_output_dims': [None],
     'shape':['brick','long_funnel'],
     'optimizer': [Adam, Nadam, RMSprop],
     'losses': [logcosh, binary_crossentropy],
     'activation':[relu, elu],
     'last_activation': [sigmoid]}

In [ ]:
model = get_model(params)
train_my_model()

In [15]:
def train_model(params, _model, generators):
    model_name = params["network_name"]
    num_train_img = 4604
    num_val_img = 1094

    np.random.seed(seed)
    log_time = time()
    params['log_time'] = log_time
    batch_size = params.get("batch_size")

    train_generator, validation_generator = generators
    _model.compile(loss = "categorical_crossentropy", optimizer = params["optimizer"], metrics=["accuracy"])


    base = '/data/oxford102/experiments'
    path = os.path.join(base, str(log_time))
    checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
    tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
    csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

    try:
        if not os.path.exists(path):
            os.makedirs(path)
        history_callback = _model.fit_generator(
                train_generator,
                steps_per_epoch=num_train_img // batch_size,
                epochs=params["epochs"],
                validation_data=validation_generator,
                validation_steps=num_val_img // params["batch_size"],
                callbacks = [checkpoint, early, tensorboard, csv_logger])
    except Exception as e:
        raise(e)
    finally:
        params.pop("optimizer")
        pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
        _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
        print(params)
        params

In [33]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(batch_size, params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

80142336/80134624 [==============================] - 2s 0us/step


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

TypeError: can't pickle _thread.RLock objects

In [13]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 512,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

ResourceExhaustedError: OOM when allocating tensor with shape[512,64,256,256] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node block1_conv1/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](block1_conv1/convolution-0-TransposeNHWCToNCHW-LayoutOptimizer, block1_conv1/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node loss/mul/_283}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_834_loss/mul", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated ten

In [14]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [17]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_5 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [15]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [16]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_4 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [18]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_6 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

{'network_name': 'vgg19', 'image_aug': False, 'optimizer_name': 'RMSprop', 'optimizer_params': None, 'batch_size': 8, 'epochs': 100, 'image_size': (256, 256), 'log_time': 1545013813.496132}


# SGD

In [12]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

ResourceExhaustedError: OOM when allocating tensor with shape[256,64,256,256] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node block1_conv2/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](block1_conv1/Relu, block1_conv2/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.


In [13]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [14]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [15]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_4 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [16]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_5 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [17]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_6 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [18]:
print("DONE")

DONE


# inception_resnet_v2 RMSProp

In [14]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_204 (Conv2D)             (None, 127, 127, 32) 864         input_2[0][0]                    
__________________________________________________________________________________________________
batch_normalization_205 (BatchN (None, 127, 127, 32) 96          conv2d_204[0][0]                 
__________________________________________________________________________________________________
activation_204 (Activation)     (None, 127, 127, 32) 0           batch_normalization_205[0][0]    
__________________________________________________________________________________________________
conv2d_205

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 91s 5s/step - loss: 2.8596 - acc: 0.3658 - val_loss: 1.9975 - val_acc: 0.5020

Epoch 00001: val_acc improved from -inf to 0.50195, saving model to /data/oxford102/experiments/1545100924.6199474/inception_resnet_v2_1545100924.6199474.h5
Epoch 2/100
17/17 [==============================] - 81s 5s/step - loss: 1.2842 - acc: 0.7020 - val_loss: 1.5761 - val_acc: 0.6134

Epoch 00002: val_acc improved from 0.50195 to 0.61337, saving model to /data/oxford102/experiments/1545100924.6199474/inception_resnet_v2_1545100924.6199474.h5
Epoch 3/100
17/17 [==============================] - 74s 4s/step - loss: 0.7966 - acc: 0.8435 - val_loss: 1.3682 - val_acc: 0.6814

Epoch 00003: val_acc improved from 0.61337 to 0.68138, saving model to /data/oxford102/experiments/1545100924.6199474/inception_resnet_v2_1545100924.6199474.h5
Epoch 4/100
17/17 [====================

In [15]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_407 (Conv2D)             (None, 127, 127, 32) 864         input_3[0][0]                    
__________________________________________________________________________________________________
batch_normalization_409 (BatchN (None, 127, 127, 32) 96          conv2d_407[0][0]                 
__________________________________________________________________________________________________
activation_407 (Activation)     (None, 127, 127, 32) 0           batch_normalization_409[0][0]    
__________________________________________________________________________________________________
conv2d_408

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 90s 3s/step - loss: 2.7810 - acc: 0.3741 - val_loss: 2.0127 - val_acc: 0.5137

Epoch 00001: val_acc improved from -inf to 0.51367, saving model to /data/oxford102/experiments/1545102712.188949/inception_resnet_v2_1545102712.188949.h5
Epoch 2/100
35/35 [==============================] - 82s 2s/step - loss: 1.2956 - acc: 0.7146 - val_loss: 1.5882 - val_acc: 0.6149

Epoch 00002: val_acc improved from 0.51367 to 0.61491, saving model to /data/oxford102/experiments/1545102712.188949/inception_resnet_v2_1545102712.188949.h5
Epoch 3/100
35/35 [==============================] - 79s 2s/step - loss: 0.7901 - acc: 0.8509 - val_loss: 1.3665 - val_acc: 0.6739

Epoch 00003: val_acc improved from 0.61491 to 0.67391, saving model to /data/oxford102/experiments/1545102712.188949/inception_resnet_v2_1545102712.188949.h5
Epoch 4/100
35/35 [==========================

In [16]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_610 (Conv2D)             (None, 127, 127, 32) 864         input_4[0][0]                    
__________________________________________________________________________________________________
batch_normalization_613 (BatchN (None, 127, 127, 32) 96          conv2d_610[0][0]                 
__________________________________________________________________________________________________
activation_610 (Activation)     (None, 127, 127, 32) 0           batch_normalization_613[0][0]    
__________________________________________________________________________________________________
conv2d_611

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
71/71 [==============================] - 96s 1s/step - loss: 2.7047 - acc: 0.3939 - val_loss: 2.0130 - val_acc: 0.5377

Epoch 00001: val_acc improved from -inf to 0.53768, saving model to /data/oxford102/experiments/1545104045.7045286/inception_resnet_v2_1545104045.7045286.h5
Epoch 2/100
71/71 [==============================] - 88s 1s/step - loss: 1.3937 - acc: 0.7104 - val_loss: 1.6368 - val_acc: 0.6204

Epoch 00002: val_acc improved from 0.53768 to 0.62039, saving model to /data/oxford102/experiments/1545104045.7045286/inception_resnet_v2_1545104045.7045286.h5
Epoch 3/100
71/71 [==============================] - 87s 1s/step - loss: 0.8712 - acc: 0.8345 - val_loss: 1.3232 - val_acc: 0.6835

Epoch 00003: val_acc improved from 0.62039 to 0.68350, saving model to /data/oxford102/experiments/1545104045.7045286/inception_resnet_v2_1545104045.7045286.h5
Epoch 4/100
71/71 [====================

In [17]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_5 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_813 (Conv2D)             (None, 127, 127, 32) 864         input_5[0][0]                    
__________________________________________________________________________________________________
batch_normalization_817 (BatchN (None, 127, 127, 32) 96          conv2d_813[0][0]                 
__________________________________________________________________________________________________
activation_813 (Activation)     (None, 127, 127, 32) 0           batch_normalization_817[0][0]    
__________________________________________________________________________________________________
conv2d_814

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
143/143 [==============================] - 105s 735ms/step - loss: 2.8658 - acc: 0.3680 - val_loss: 2.2568 - val_acc: 0.4871

Epoch 00001: val_acc improved from -inf to 0.48713, saving model to /data/oxford102/experiments/1545105650.426833/inception_resnet_v2_1545105650.426833.h5
Epoch 2/100
143/143 [==============================] - 98s 684ms/step - loss: 1.6053 - acc: 0.6481 - val_loss: 1.6935 - val_acc: 0.5951

Epoch 00002: val_acc improved from 0.48713 to 0.59510, saving model to /data/oxford102/experiments/1545105650.426833/inception_resnet_v2_1545105650.426833.h5
Epoch 3/100
143/143 [==============================] - 98s 688ms/step - loss: 1.0455 - acc: 0.7893 - val_loss: 1.4787 - val_acc: 0.6422

Epoch 00003: val_acc improved from 0.59510 to 0.64218, saving model to /data/oxford102/experiments/1545105650.426833/inception_resnet_v2_1545105650.426833.h5
Epoch 4/100
143/143 [========

In [18]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1016 (Conv2D)            (None, 127, 127, 32) 864         input_6[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1021 (Batch (None, 127, 127, 32) 96          conv2d_1016[0][0]                
__________________________________________________________________________________________________
activation_1016 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1021[0][0]   
__________________________________________________________________________________________________
conv2d_101

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
287/287 [==============================] - 126s 439ms/step - loss: 3.0857 - acc: 0.3341 - val_loss: 2.6159 - val_acc: 0.4265

Epoch 00001: val_acc improved from -inf to 0.42647, saving model to /data/oxford102/experiments/1545107391.954375/inception_resnet_v2_1545107391.954375.h5
Epoch 2/100
287/287 [==============================] - 119s 415ms/step - loss: 2.0246 - acc: 0.5698 - val_loss: 2.0688 - val_acc: 0.5371

Epoch 00002: val_acc improved from 0.42647 to 0.53711, saving model to /data/oxford102/experiments/1545107391.954375/inception_resnet_v2_1545107391.954375.h5
Epoch 3/100
287/287 [==============================] - 119s 416ms/step - loss: 1.5126 - acc: 0.6742 - val_loss: 1.8192 - val_acc: 0.5909

Epoch 00003: val_acc improved from 0.53711 to 0.59091, saving model to /data/oxford102/experiments/1545107391.954375/inception_resnet_v2_1545107391.954375.h5
Epoch 4/100
287/287 [======

In [19]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_7 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1219 (Conv2D)            (None, 127, 127, 32) 864         input_7[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1225 (Batch (None, 127, 127, 32) 96          conv2d_1219[0][0]                
__________________________________________________________________________________________________
activation_1219 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1225[0][0]   
__________________________________________________________________________________________________
conv2d_122

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
575/575 [==============================] - 163s 283ms/step - loss: 3.5114 - acc: 0.2611 - val_loss: 3.1176 - val_acc: 0.3410

Epoch 00001: val_acc improved from -inf to 0.34099, saving model to /data/oxford102/experiments/1545109745.7254472/inception_resnet_v2_1545109745.7254472.h5
Epoch 2/100
575/575 [==============================] - 156s 271ms/step - loss: 2.7649 - acc: 0.4157 - val_loss: 2.7685 - val_acc: 0.4282

Epoch 00002: val_acc improved from 0.34099 to 0.42818, saving model to /data/oxford102/experiments/1545109745.7254472/inception_resnet_v2_1545109745.7254472.h5
Epoch 3/100
575/575 [==============================] - 156s 272ms/step - loss: 2.3784 - acc: 0.5020 - val_loss: 2.5533 - val_acc: 0.4411

Epoch 00003: val_acc improved from 0.42818 to 0.44107, saving model to /data/oxford102/experiments/1545109745.7254472/inception_resnet_v2_1545109745.7254472.h5
Epoch 4/100
575/575 [

# SGD

In [21]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_8 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1422 (Conv2D)            (None, 127, 127, 32) 864         input_8[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1429 (Batch (None, 127, 127, 32) 96          conv2d_1422[0][0]                
__________________________________________________________________________________________________
activation_1422 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1429[0][0]   
__________________________________________________________________________________________________
conv2d_142

Total params: 111,069,510
Trainable params: 56,730,726
Non-trainable params: 54,338,784
__________________________________________________________________________________________________
Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 86s 5s/step - loss: 3.3373 - acc: 0.2654 - val_loss: 2.3692 - val_acc: 0.4297

Epoch 00001: val_acc improved from -inf to 0.42969, saving model to /data/oxford102/experiments/1545136890.5101461/inception_resnet_v2_1545136890.5101461.h5
Epoch 2/100
17/17 [==============================] - 75s 4s/step - loss: 1.6233 - acc: 0.6077 - val_loss: 1.7177 - val_acc: 0.5800

Epoch 00002: val_acc improved from 0.42969 to 0.57995, saving model to /data/oxford102/experiments/1545136890.5101461/inception_resnet_v2_1545136890.5101461.h5
Epoch 3/100
17/17 [==============================] - 75s 4s/step - loss: 0.9855 - acc: 0.7780 - val_loss: 1.4433 - val_acc: 0.6432

Epoch 00003:

In [22]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_9 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1625 (Conv2D)            (None, 127, 127, 32) 864         input_9[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1633 (Batch (None, 127, 127, 32) 96          conv2d_1625[0][0]                
__________________________________________________________________________________________________
activation_1625 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1633[0][0]   
__________________________________________________________________________________________________
conv2d_162

Total params: 111,069,510
Trainable params: 56,730,726
Non-trainable params: 54,338,784
__________________________________________________________________________________________________
Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 92s 3s/step - loss: 2.9695 - acc: 0.3295 - val_loss: 2.0891 - val_acc: 0.4863

Epoch 00001: val_acc improved from -inf to 0.48633, saving model to /data/oxford102/experiments/1545139627.81609/inception_resnet_v2_1545139627.81609.h5
Epoch 2/100
35/35 [==============================] - 80s 2s/step - loss: 1.4069 - acc: 0.6581 - val_loss: 1.5320 - val_acc: 0.6294

Epoch 00002: val_acc improved from 0.48633 to 0.62940, saving model to /data/oxford102/experiments/1545139627.81609/inception_resnet_v2_1545139627.81609.h5
Epoch 3/100
35/35 [==============================] - 81s 2s/step - loss: 0.8705 - acc: 0.7971 - val_loss: 1.2603 - val_acc: 0.6874

Epoch 00003: val_acc

In [23]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_10 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1828 (Conv2D)            (None, 127, 127, 32) 864         input_10[0][0]                   
__________________________________________________________________________________________________
batch_normalization_1837 (Batch (None, 127, 127, 32) 96          conv2d_1828[0][0]                
__________________________________________________________________________________________________
activation_1828 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1837[0][0]   
__________________________________________________________________________________________________
conv2d_182

__________________________________________________________________________________________________
activation_1999 (Activation)    (None, 6, 6, 192)    0           batch_normalization_2008[0][0]   
__________________________________________________________________________________________________
activation_2002 (Activation)    (None, 6, 6, 256)    0           batch_normalization_2011[0][0]   
__________________________________________________________________________________________________
block8_3_mixed (Concatenate)    (None, 6, 6, 448)    0           activation_1999[0][0]            
                                                                 activation_2002[0][0]            
__________________________________________________________________________________________________
block8_3_conv (Conv2D)          (None, 6, 6, 2080)   933920      block8_3_mixed[0][0]             
__________________________________________________________________________________________________
block8_3 (

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
71/71 [==============================] - 98s 1s/step - loss: 2.8970 - acc: 0.3356 - val_loss: 2.0948 - val_acc: 0.4807

Epoch 00001: val_acc improved from -inf to 0.48070, saving model to /data/oxford102/experiments/1545142419.7855225/inception_resnet_v2_1545142419.7855225.h5
Epoch 2/100
71/71 [==============================] - 88s 1s/step - loss: 1.4806 - acc: 0.6362 - val_loss: 1.6758 - val_acc: 0.5680

Epoch 00002: val_acc improved from 0.48070 to 0.56796, saving model to /data/oxford102/experiments/1545142419.7855225/inception_resnet_v2_1545142419.7855225.h5
Epoch 3/100
71/71 [==============================] - 88s 1s/step - loss: 1.0286 - acc: 0.7590 - val_loss: 1.4406 - val_acc: 0.6243

Epoch 00003: val_acc improved from 0.56796 to 0.62427, saving model to /data/oxford102/experiments/1545142419.7855225/inception_resnet_v2_1545142419.7855225.h5
Epoch 4/100
71/71 [====================

In [24]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_11 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_2031 (Conv2D)            (None, 127, 127, 32) 864         input_11[0][0]                   
__________________________________________________________________________________________________
batch_normalization_2041 (Batch (None, 127, 127, 32) 96          conv2d_2031[0][0]                
__________________________________________________________________________________________________
activation_2031 (Activation)    (None, 127, 127, 32) 0           batch_normalization_2041[0][0]   
__________________________________________________________________________________________________
conv2d_203

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
143/143 [==============================] - 108s 758ms/step - loss: 2.9583 - acc: 0.3140 - val_loss: 2.2570 - val_acc: 0.4320

Epoch 00001: val_acc improved from -inf to 0.43199, saving model to /data/oxford102/experiments/1545146219.344922/inception_resnet_v2_1545146219.344922.h5
Epoch 2/100
143/143 [==============================] - 99s 689ms/step - loss: 1.7221 - acc: 0.5611 - val_loss: 1.9309 - val_acc: 0.5009

Epoch 00002: val_acc improved from 0.43199 to 0.50094, saving model to /data/oxford102/experiments/1545146219.344922/inception_resnet_v2_1545146219.344922.h5
Epoch 3/100
143/143 [==============================] - 98s 684ms/step - loss: 1.4276 - acc: 0.6421 - val_loss: 1.7872 - val_acc: 0.5301

Epoch 00003: val_acc improved from 0.50094 to 0.53013, saving model to /data/oxford102/experiments/1545146219.344922/inception_resnet_v2_1545146219.344922.h5
Epoch 4/100
143/143 [========

In [25]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_12 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_2234 (Conv2D)            (None, 127, 127, 32) 864         input_12[0][0]                   
__________________________________________________________________________________________________
batch_normalization_2245 (Batch (None, 127, 127, 32) 96          conv2d_2234[0][0]                
__________________________________________________________________________________________________
activation_2234 (Activation)    (None, 127, 127, 32) 0           batch_normalization_2245[0][0]   
__________________________________________________________________________________________________
conv2d_223

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
287/287 [==============================] - 127s 443ms/step - loss: 3.1368 - acc: 0.2655 - val_loss: 2.6137 - val_acc: 0.3355

Epoch 00001: val_acc improved from -inf to 0.33548, saving model to /data/oxford102/experiments/1545148489.372287/inception_resnet_v2_1545148489.372287.h5
Epoch 2/100
287/287 [==============================] - 118s 410ms/step - loss: 2.3317 - acc: 0.4012 - val_loss: 2.4211 - val_acc: 0.3720

Epoch 00002: val_acc improved from 0.33548 to 0.37199, saving model to /data/oxford102/experiments/1545148489.372287/inception_resnet_v2_1545148489.372287.h5
Epoch 3/100
287/287 [==============================] - 118s 411ms/step - loss: 2.2449 - acc: 0.4215 - val_loss: 2.4361 - val_acc: 0.3720

Epoch 00003: val_acc did not improve from 0.37199
Epoch 4/100
287/287 [==============================] - 117s 408ms/step - loss: 2.2479 - acc: 0.4014 - val_loss: 2.5018 - val_acc: 0.371

In [26]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_13 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_2437 (Conv2D)            (None, 127, 127, 32) 864         input_13[0][0]                   
__________________________________________________________________________________________________
batch_normalization_2449 (Batch (None, 127, 127, 32) 96          conv2d_2437[0][0]                
__________________________________________________________________________________________________
activation_2437 (Activation)    (None, 127, 127, 32) 0           batch_normalization_2449[0][0]   
__________________________________________________________________________________________________
conv2d_243

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.


FailedPreconditionError: Attempting to use uninitialized value dense_25/bias
	 [[{{node dense_25/bias/_114256}} = _Send[T=DT_FLOAT, client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_6_dense_25/bias", _device="/job:localhost/replica:0/task:0/device:GPU:0"](dense_25/bias)]]

In [ ]:
print("Done")

In [17]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

In [24]:
for network in ['inception_resnet_v2', 'vgg16', 'vgg19', 'mobilenet_v2']:
    for lr in [0.1, 0.01, 0.001]:
        for momentum in [0.5, 0.75, 0.9]:
            for decay in [0.01, 0.1, 0.2]:
                for nesterov in [True, False]:
                    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
                    params['optimizer'] = _optimizer
                    _model, input_processor = get_model(params["network_name"])
                    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
                    train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_610 (Conv2D)             (None, 127, 127, 32) 864         input_4[0][0]                    
__________________________________________________________________________________________________
batch_normalization_613 (BatchN (None, 127, 127, 32) 96          conv2d_610[0][0]                 
__________________________________________________________________________________________________
activation_610 (Activation)     (None, 127, 127, 32) 0           batch_normalization_613[0][0]    
__________________________________________________________________________________________________
conv2d_611

__________________________________________________________________________________________________
batch_normalization_771 (BatchN (None, 14, 14, 256)  768         conv2d_768[0][0]                 
__________________________________________________________________________________________________
batch_normalization_774 (BatchN (None, 14, 14, 288)  864         conv2d_771[0][0]                 
__________________________________________________________________________________________________
activation_766 (Activation)     (None, 14, 14, 256)  0           batch_normalization_769[0][0]    
__________________________________________________________________________________________________
activation_768 (Activation)     (None, 14, 14, 256)  0           batch_normalization_771[0][0]    
__________________________________________________________________________________________________
activation_771 (Activation)     (None, 14, 14, 288)  0           batch_normalization_774[0][0]    
__________

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 96s 3s/step - loss: 2.9269 - acc: 0.3404 - val_loss: 2.1022 - val_acc: 0.4893

Epoch 00001: val_acc improved from -inf to 0.48926, saving model to /data/oxford102/experiments/1545358483.3476398/inception_resnet_v2_1545358483.3476398.h5
Epoch 2/100
35/35 [==============================] - 88s 3s/step - loss: 1.5070 - acc: 0.6436 - val_loss: 1.6492 - val_acc: 0.5849

Epoch 00002: val_acc improved from 0.48926 to 0.58489, saving model to /data/oxford102/experiments/1545358483.3476398/inception_resnet_v2_1545358483.3476398.h5
Epoch 3/100
35/35 [==============================] - 82s 2s/step - loss: 0.9904 - acc: 0.7747 - val_loss: 1.4124 - val_acc: 0.6439

Epoch 00003: val_acc improved from 0.58489 to 0.64389, saving model to /data/oxford102/experiments/1545358483.3476398/inception_resnet_v2_1545358483.3476398.h5
Epoch 4/100
35/35 [====================

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


...

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 92s 3s/step - loss: 3.1112 - acc: 0.2933 - val_loss: 2.4885 - val_acc: 0.3975

Epoch 00001: val_acc improved from -inf to 0.39746, saving model to /data/oxford102/experiments/1545370714.5285096/inception_resnet_v2_1545370714.5285096.h5
Epoch 2/100
35/35 [==============================] - 82s 2s/step - loss: 1.9716 - acc: 0.5348 - val_loss: 2.1244 - val_acc: 0.4917

Epoch 00002: val_acc improved from 0.39746 to 0.49172, saving model to /data/oxford102/experiments/1545370714.5285096/inception_resnet_v2_1545370714.5285096.h5
Epoch 3/100
35/35 [==============================] - 82s 2s/step - loss: 1.6196 - acc: 0.6215 - val_loss: 1.9908 - val_acc: 0.5331

Epoch 00003: val_acc improved from 0.49172 to 0.53313, saving model to /data/oxford102/experiments/1545370714.5285096/inception_resnet_v2_1545370714.5285096.h5
Epoch 4/100
35/35 [====================

__________________________________________________________________________________________________
flatten_10 (Flatten)            (None, 55296)        0           conv_7b_ac[0][0]                 
__________________________________________________________________________________________________
dense_19 (Dense)                (None, 1024)         56624128    flatten_10[0][0]                 
__________________________________________________________________________________________________
dropout_10 (Dropout)            (None, 1024)         0           dense_19[0][0]                   
__________________________________________________________________________________________________
batch_normalization_2040 (Batch (None, 1024)         4096        dropout_10[0][0]                 
__________________________________________________________________________________________________
dense_20 (Dense)                (None, 102)          104550      batch_normalization_2040[0][0]   
Total para

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 95s 3s/step - loss: 2.9406 - acc: 0.3183 - val_loss: 2.1408 - val_acc: 0.4385

Epoch 00001: val_acc improved from -inf to 0.43848, saving model to /data/oxford102/experiments/1545375950.4201324/inception_resnet_v2_1545375950.4201324.h5
Epoch 2/100
35/35 [==============================] - 82s 2s/step - loss: 1.4775 - acc: 0.6103 - val_loss: 1.5512 - val_acc: 0.5859

Epoch 00002: val_acc improved from 0.43848 to 0.58592, saving model to /data/oxford102/experiments/1545375950.4201324/inception_resnet_v2_1545375950.4201324.h5
Epoch 3/100
35/35 [==============================] - 82s 2s/step - loss: 0.9927 - acc: 0.7459 - val_loss: 1.3488 - val_acc: 0.6439

Epoch 00003: val_acc improved from 0.58592 to 0.64389, saving model to /data/oxford102/experiments/1545375950.4201324/inception_resnet_v2_1545375950.4201324.h5
Epoch 4/100
35/35 [====================

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 96s 3s/step - loss: 2.9708 - acc: 0.3187 - val_loss: 2.3204 - val_acc: 0.4160

Epoch 00001: val_acc improved from -inf to 0.41602, saving model to /data/oxford102/experiments/1545378900.588706/inception_resnet_v2_1545378900.588706.h5
Epoch 2/100
35/35 [==============================] - 84s 2s/step - loss: 1.7634 - acc: 0.5623 - val_loss: 1.9621 - val_acc: 0.5041

Epoch 00002: val_acc improved from 0.41602 to 0.50414, saving model to /data/oxford102/experiments/1545378900.588706/inception_resnet_v2_1545378900.588706.h5
Epoch 3/100
35/35 [==============================] - 85s 2s/step - loss: 1.3931 - acc: 0.6626 - val_loss: 1.6963 - val_acc: 0.5642

Epoch 00003: val_acc improved from 0.50414 to 0.56418, saving model to /data/oxford102/experiments/1545378900.588706/inception_resnet_v2_1545378900.588706.h5
Epoch 4/100
34/35 [==========================

ResourceExhaustedError: OOM when allocating tensor with shape[128,64,125,125] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node conv2d_2236/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](activation_2235/Relu, conv2d_2236/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node loss_8/mul/_101515}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_4540_loss_8/mul", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_te

In [ ]:
print("DONE")

In [ ]:
lr=0.001
momentum = 0.9
decay = 0.1
nesterov = False
_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

In [ ]:
#inception_resnet_v2, vgg16, vgg19, mobilenet_v2

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

In [ ]:
import itertools

In [70]:
for batch_size in [256, 128, 64, 32]:
    for network_name in ["inception_resnet_v2", "vgg16", "vgg19"]:
        for lr in [0.001, 0.01, 0.1]:
            for optimizer in [optimizers.RMSprop(lr=lr, rho=0.9, epsilon=None, decay=0.0),
                              optimizers.SGD(lr=lr, decay=1e-6, momentum=0.9, nesterov=True), 
                              optimizers.Adagrad(lr=lr, epsilon=None, decay=0.0), 
                              optimizers.Adadelta(lr=lr, rho=0.95, epsilon=None, decay=0.0),
                              optimizers.Adam(lr=lr, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False),
                              optimizers.Adamax(lr=lr, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0),
                              optimizers.Nadam(lr=lr, beta_1=0.9, beta_2=0.999, epsilon=None, schedule_decay=0.004)]:
                optimizer_name = ("RMSprop" if "RMSprop" in str(optimizer) else
                                  "SGD" if "SGD" in str(optimizer) else 
                                  "Adagrad" if "Adagrad" in str(optimizer) else 
                                  "Adadelta" if "Adadelta" in str(optimizer) else 
                                  "Adam" if "Adam" in str(optimizer) else 
                                  "Adamax" if "Adamax" in str(optimizer) else 
                                  "Nadam" if "Nadam" in str(optimizer) else None)
            
            
                #inception_resnet_v2, vgg16, vgg19, mobilenet_v2

                params = {'network_name': network_name,
                         'image_aug': False,
                         'optimizer_name': optimizer_name, 
                         'optimizer': optimizer,
                         'optimizer_params': None, 
                         'batch_size': batch_size,
                         'epochs': 150,
                         'image_size': (256, 256),
                         'log_time': None}

                _model, input_processor = get_model(params["network_name"])
                train_generator, validation_generator = get_generators(batch_size, params["image_size"], input_processor)
                train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_813 (Conv2D)             (None, 127, 127, 32) 864         input_6[0][0]                    
__________________________________________________________________________________________________
batch_normalization_818 (BatchN (None, 127, 127, 32) 96          conv2d_813[0][0]                 
__________________________________________________________________________________________________
activation_813 (Activation)     (None, 127, 127, 32) 0           batch_normalization_818[0][0]    
__________________________________________________________________________________________________
conv2d_814

activation_992 (Activation)     (None, 6, 6, 192)    0           batch_normalization_997[0][0]    
__________________________________________________________________________________________________
activation_995 (Activation)     (None, 6, 6, 256)    0           batch_normalization_1000[0][0]   
__________________________________________________________________________________________________
block8_5_mixed (Concatenate)    (None, 6, 6, 448)    0           activation_992[0][0]             
                                                                 activation_995[0][0]             
__________________________________________________________________________________________________
block8_5_conv (Conv2D)          (None, 6, 6, 2080)   933920      block8_5_mixed[0][0]             
__________________________________________________________________________________________________
block8_5 (Lambda)               (None, 6, 6, 2080)   0           block8_4_ac[0][0]                
          

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/150
8/8 [==============================] - 95s 12s/step - loss: 3.1314 - acc: 0.3137 - val_loss: 2.2016 - val_acc: 0.4473

Epoch 00001: val_acc improved from -inf to 0.44727, saving model to /data/oxford102/experiments/1544929307.4675195/mobilenet_v2_1544929307.4675195.h5
Epoch 2/150
8/8 [==============================] - 81s 10s/step - loss: 1.4652 - acc: 0.6521 - val_loss: 1.7202 - val_acc: 0.5722

Epoch 00002: val_acc improved from 0.44727 to 0.57216, saving model to /data/oxford102/experiments/1544929307.4675195/mobilenet_v2_1544929307.4675195.h5
Epoch 3/150
8/8 [==============================] - 67s 8s/step - loss: 0.9539 - acc: 0.7824 - val_loss: 1.2862 - val_acc: 0.6976

Epoch 00003: val_acc improved from 0.57216 to 0.69759, saving model to /data/oxford102/experiments/1544929307.4675195/mobilenet_v2_1544929307.4675195.h5
Epoch 4/150
8/8 [==============================] - 73s 9s/step -

ResourceExhaustedError: OOM when allocating tensor with shape[508,64,125,125] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node conv2d_815/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](activation_814/Relu, conv2d_815/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node metrics_3/acc/Mean/_39615}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_4582_metrics_3/acc/Mean", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated tensors when OOM happens, a

In [16]:
#inception_resnet_v2, vgg16, vgg19, mobilenet_v2

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

NameError: name 'num_train_img' is not defined

In [37]:
dir(optimizers.RMSprop)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__slotnames__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'from_config',
 'get_config',
 'get_gradients',
 'get_updates',
 'get_weights',
 'set_weights']

In [47]:
optimizer = optimizers.SGD

In [53]:
optimizer_name = ("RMSprop" if "RMSprop" in str(optimizer) else "SGD" if "SGD" in str(optimizer) else None)

In [54]:
optimizer_name

'SGD'

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
35/35 [==============================] - 30s 861ms/step - loss: 3.5846 - acc: 0.2348 - val_loss: 3.0738 - val_acc: 0.3203

Epoch 00001: val_acc improved from -inf to 0.32031, saving model to /data/oxford102/experiments/1544313888.896595/mobilenet_v2_1544313888.896595.h5
Epoch 2/100
35/35 [==============================] - 24s 679ms/step - loss: 2.8652 - acc: 0.3402 - val_loss: 2.7228 - val_acc: 0.3711

Epoch 00002: val_acc improved from 0.32031 to 0.37109, saving model to /data/oxford102/experiments/1544313888.896595/mobilenet_v2_1544313888.896595.h5
Epoch 3/100
35/35 [==============================] - 24s 684ms/step - loss: 2.5635 - acc: 0.4232 - val_loss: 2.3986 - val_acc: 0.4766

Epoch 00003: val_acc improved from 0.37109 to 0.47656, saving model to /data/oxford102/experiments/1544313888.896595/mobilenet_v2_1544313888.896595.h5
Epoch 4/100
35/35 [==============================] - 24s 683ms/step - loss: 2.4074 - acc: 0.4580 - val_loss: 2.2437 - val_acc: 0.5156

Epoch 0000

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
71/71 [==============================] - 55s 769ms/step - loss: 3.1814 - acc: 0.3072 - val_loss: 2.6400 - val_acc: 0.4320

Epoch 00001: val_acc improved from -inf to 0.43199, saving model to /data/oxford102/experiments/1544321516.4379833/mobilenet_v2_1544321516.4379833.h5
Epoch 2/100
71/71 [==============================] - 49s 685ms/step - loss: 2.4163 - acc: 0.4626 - val_loss: 2.2147 - val_acc: 0.5055

Epoch 00002: val_acc improved from 0.43199 to 0.50551, saving model to /data/oxford102/experiments/1544321516.4379833/mobilenet_v2_1544321516.4379833.h5
Epoch 3/100
71/71 [==============================] - 50s 704ms/step - loss: 1.6797 - acc: 0.6342 - val_loss: 1.9133 - val_acc: 0.5695

Epoch 00003: val_acc improved from 0.50551 to 0.56950, saving model to /data/oxford102/experiments/1544321516.4379833/mobilenet_v2_1544321516.4379833.h5
Epoch 4/100
71/71 [==============================] - 49s 688ms/step - loss: 1.5051 - acc: 0.6774 - val_loss: 1.6431 - val_acc: 0.6121

Epoc

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
143/143 [==============================] - 104s 728ms/step - loss: 2.8257 - acc: 0.3722 - val_loss: 2.2077 - val_acc: 0.5000

Epoch 00001: val_acc improved from -inf to 0.50000, saving model to /data/oxford102/experiments/1544322364.962447/mobilenet_v2_1544322364.962447.h5
Epoch 2/100
143/143 [==============================] - 99s 692ms/step - loss: 1.6082 - acc: 0.6630 - val_loss: 1.7285 - val_acc: 0.6036

Epoch 00002: val_acc improved from 0.50000 to 0.60358, saving model to /data/oxford102/experiments/1544322364.962447/mobilenet_v2_1544322364.962447.h5
Epoch 3/100
143/143 [==============================] - 98s 684ms/step - loss: 1.0723 - acc: 0.7830 - val_loss: 1.4895 - val_acc: 0.6375

Epoch 00003: val_acc improved from 0.60358 to 0.63748, saving model to /data/oxford102/experiments/1544322364.962447/mobilenet_v2_1544322364.962447.h5
Epoch 4/100
143/143 [==============================] - 98s 683ms/step - loss: 0.7257 - acc: 0.8654 - val_loss: 1.2789 - val_acc: 0.6836

E

In [11]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'mobilenet_v2',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
287/287 [==============================] - 204s 711ms/step - loss: 2.1876 - acc: 0.5239 - val_loss: 1.6708 - val_acc: 0.6093

Epoch 00001: val_acc improved from -inf to 0.60930, saving model to /data/oxford102/experiments/1544324718.4162903/mobilenet_v2_1544324718.4162903.h5
Epoch 2/100
287/287 [==============================] - 196s 682ms/step - loss: 0.8537 - acc: 0.8272 - val_loss: 1.3012 - val_acc: 0.6784

Epoch 00002: val_acc improved from 0.60930 to 0.67844, saving model to /data/oxford102/experiments/1544324718.4162903/mobilenet_v2_1544324718.4162903.h5
Epoch 3/100
287/287 [==============================] - 196s 683ms/step - loss: 0.4377 - acc: 0.9240 - val_loss: 1.1310 - val_acc: 0.7269

Epoch 00003: val_acc improved from 0.67844 to 0.72693, saving model to /data/oxford102/experiments/1544324718.4162903/mobilenet_v2_1544324718.4162903.h5
Epoch 4/100
287/287 [==============================] - 196s 683ms/step - loss: 0.2630 - acc: 0.9578 - val_loss: 1.1568 - val_acc: 

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'mobilenet_v2',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
575/575 [==============================] - 403s 701ms/step - loss: 1.5411 - acc: 0.6723 - val_loss: 1.3399 - val_acc: 0.6692

Epoch 00001: val_acc improved from -inf to 0.66916, saving model to /data/oxford102/experiments/1544399249.5668316/mobilenet_v2_1544399249.5668316.h5
Epoch 2/100
575/575 [==============================] - 393s 683ms/step - loss: 0.3679 - acc: 0.9373 - val_loss: 1.1550 - val_acc: 0.7090

Epoch 00002: val_acc improved from 0.66916 to 0.70904, saving model to /data/oxford102/experiments/1544399249.5668316/mobilenet_v2_1544399249.5668316.h5
Epoch 3/100
575/575 [==============================] - 392s 682ms/step - loss: 0.1783 - acc: 0.9726 - val_loss: 1.1863 - val_acc: 0.7048

Epoch 00003: val_acc did not improve from 0.70904
Epoch 4/100
575/575 [==============================] - 392s 682ms/step - loss: 0.1210 - acc: 0.9810 - val_loss: 1.1200 - val_acc: 0.7149

Epoch 00004: val_acc improved from 0.70904 to 0.71492, saving model to /data/oxford102/experime

# RUN BATCHE SIZES SEQUENTIAL (no restart of kernel)

In [13]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 512,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
8/8 [==============================] - 9s 1s/step - loss: 0.1649 - acc: 0.9844 - val_loss: 1.1774 - val_acc: 0.7344

Epoch 00001: val_acc improved from -inf to 0.73438, saving model to /data/oxford102/experiments/1544329528.7978303/mobilenet_v2_1544329528.7978303.h5
Epoch 2/100
8/8 [==============================] - 6s 698ms/step - loss: 0.2239 - acc: 0.9727 - val_loss: 1.2865 - val_acc: 0.6875

Epoch 00002: val_acc did not improve from 0.73438
Epoch 3/100
8/8 [==============================] - 5s 683ms/step - loss: 0.2118 - acc: 0.9688 - val_loss: 1.0640 - val_acc: 0.7812

Epoch 00003: val_acc improved from 0.73438 to 0.78125, saving model to /data/oxford102/experiments/1544329528.7978303/mobilenet_v2_1544329528.7978303.h5
Epoch 4/100
8/8 [==============================] - 6s 688ms/step - loss: 0.1862 - acc: 0.9766 - val_loss: 1.4649 - val_acc: 0.6094

Epoch 00004: val_acc did not improve from 0.78125
Epoch 5/100
8/8 [==============================] - 5s 684ms/step - loss:

In [14]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
17/17 [==============================] - 17s 982ms/step - loss: 0.2301 - acc: 0.9651 - val_loss: 1.3921 - val_acc: 0.6250

Epoch 00001: val_acc improved from -inf to 0.62500, saving model to /data/oxford102/experiments/1544329584.4107325/mobilenet_v2_1544329584.4107325.h5
Epoch 2/100
17/17 [==============================] - 11s 661ms/step - loss: 0.1688 - acc: 0.9816 - val_loss: 1.3094 - val_acc: 0.7157

Epoch 00002: val_acc improved from 0.62500 to 0.71569, saving model to /data/oxford102/experiments/1544329584.4107325/mobilenet_v2_1544329584.4107325.h5
Epoch 3/100
17/17 [==============================] - 12s 686ms/step - loss: 0.1453 - acc: 0.9779 - val_loss: 1.2163 - val_acc: 0.6797

Epoch 00003: val_acc did not improve from 0.71569
Epoch 4/100
17/17 [==============================] - 12s 686ms/step - loss: 0.2289 - acc: 0.9596 - val_loss: 1.0969 - val_acc: 0.7344

Epoch 00004: val_acc improved from 0.71569 to 0.73438, saving model to /data/oxford102/experiments/15443295

In [15]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
35/35 [==============================] - 28s 793ms/step - loss: 0.2139 - acc: 0.9625 - val_loss: 1.0995 - val_acc: 0.7109

Epoch 00001: val_acc improved from -inf to 0.71094, saving model to /data/oxford102/experiments/1544329740.684749/mobilenet_v2_1544329740.684749.h5
Epoch 2/100
35/35 [==============================] - 24s 680ms/step - loss: 0.1259 - acc: 0.9837 - val_loss: 1.0764 - val_acc: 0.7578

Epoch 00002: val_acc improved from 0.71094 to 0.75781, saving model to /data/oxford102/experiments/1544329740.684749/mobilenet_v2_1544329740.684749.h5
Epoch 3/100
35/35 [==============================] - 23s 671ms/step - loss: 0.1215 - acc: 0.9857 - val_loss: 1.1856 - val_acc: 0.6913

Epoch 00003: val_acc did not improve from 0.75781
Epoch 4/100
35/35 [==============================] - 24s 678ms/step - loss: 0.1274 - acc: 0.9813 - val_loss: 1.0628 - val_acc: 0.7422

Epoch 00004: val_acc did not improve from 0.75781
Epoch 5/100
35/35 [==============================] - 24s 681m

In [16]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
71/71 [==============================] - 53s 753ms/step - loss: 0.1639 - acc: 0.9762 - val_loss: 1.1253 - val_acc: 0.7181

Epoch 00001: val_acc improved from -inf to 0.71815, saving model to /data/oxford102/experiments/1544329882.089569/mobilenet_v2_1544329882.089569.h5
Epoch 2/100
71/71 [==============================] - 49s 686ms/step - loss: 0.1255 - acc: 0.9815 - val_loss: 1.1536 - val_acc: 0.7261

Epoch 00002: val_acc improved from 0.71815 to 0.72610, saving model to /data/oxford102/experiments/1544329882.089569/mobilenet_v2_1544329882.089569.h5
Epoch 3/100
71/71 [==============================] - 48s 682ms/step - loss: 0.1108 - acc: 0.9824 - val_loss: 1.1970 - val_acc: 0.6931

Epoch 00003: val_acc did not improve from 0.72610
Epoch 4/100
71/71 [==============================] - 49s 685ms/step - loss: 0.1124 - acc: 0.9810 - val_loss: 1.1961 - val_acc: 0.7316

Epoch 00004: val_acc improved from 0.72610 to 0.73162, saving model to /data/oxford102/experiments/1544329882.0

In [17]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
143/143 [==============================] - 102s 717ms/step - loss: 0.1109 - acc: 0.9803 - val_loss: 1.1367 - val_acc: 0.7241

Epoch 00001: val_acc improved from -inf to 0.72411, saving model to /data/oxford102/experiments/1544330253.19369/mobilenet_v2_1544330253.19369.h5
Epoch 2/100
143/143 [==============================] - 98s 683ms/step - loss: 0.0811 - acc: 0.9889 - val_loss: 1.2432 - val_acc: 0.7090

Epoch 00002: val_acc did not improve from 0.72411
Epoch 3/100
143/143 [==============================] - 98s 682ms/step - loss: 0.0959 - acc: 0.9847 - val_loss: 1.1647 - val_acc: 0.7260

Epoch 00003: val_acc improved from 0.72411 to 0.72599, saving model to /data/oxford102/experiments/1544330253.19369/mobilenet_v2_1544330253.19369.h5
Epoch 4/100
143/143 [==============================] - 98s 682ms/step - loss: 0.0768 - acc: 0.9886 - val_loss: 1.1317 - val_acc: 0.7250

Epoch 00004: val_acc did not improve from 0.72599
Epoch 5/100
143/143 [==============================] - 9

In [18]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
287/287 [==============================] - 201s 699ms/step - loss: 0.0806 - acc: 0.9874 - val_loss: 1.1497 - val_acc: 0.7232

Epoch 00001: val_acc improved from -inf to 0.72316, saving model to /data/oxford102/experiments/1544330862.5871413/mobilenet_v2_1544330862.5871413.h5
Epoch 2/100
287/287 [==============================] - 195s 680ms/step - loss: 0.0666 - acc: 0.9901 - val_loss: 1.1626 - val_acc: 0.7218

Epoch 00002: val_acc did not improve from 0.72316
Epoch 3/100
287/287 [==============================] - 195s 679ms/step - loss: 0.0582 - acc: 0.9915 - val_loss: 1.1660 - val_acc: 0.7194

Epoch 00003: val_acc did not improve from 0.72316
Epoch 4/100
287/287 [==============================] - 195s 679ms/step - loss: 0.0541 - acc: 0.9918 - val_loss: 1.2133 - val_acc: 0.7232

Epoch 00004: val_acc improved from 0.72316 to 0.72316, saving model to /data/oxford102/experiments/1544330862.5871413/mobilenet_v2_1544330862.5871413.h5
Epoch 5/100
287/287 [========================

In [19]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
575/575 [==============================] - 397s 690ms/step - loss: 0.0552 - acc: 0.9925 - val_loss: 1.2356 - val_acc: 0.7090

Epoch 00001: val_acc improved from -inf to 0.70904, saving model to /data/oxford102/experiments/1544332252.6100016/mobilenet_v2_1544332252.6100016.h5
Epoch 2/100
575/575 [==============================] - 391s 681ms/step - loss: 0.0414 - acc: 0.9940 - val_loss: 1.2587 - val_acc: 0.7142

Epoch 00002: val_acc improved from 0.70904 to 0.71422, saving model to /data/oxford102/experiments/1544332252.6100016/mobilenet_v2_1544332252.6100016.h5
Epoch 3/100
459/575 [======================>.......] - ETA: 1:05 - loss: 0.0390 - acc: 0.9948{'network_name': 'mobilenet_v2', 'image_aug': False, 'optimizer': 'RMSprop', 'optimizer_params': None, 'batch_size': 8, 'epochs': 100, 'image_size': (256, 256), 'log_time': 1544332252.6100016}


KeyboardInterrupt: 

# FINETUNE TOP LAYERS

In [ ]:
for i, layer in enumerate(base_model.layers[619:]):
    print(i, layer.name)
    layer.trainable = True

In [12]:
model_name = "vgg19"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'SGD',
          'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.SGD(lr=0.001, momentum=0.9), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
71/71 [==============================] - 51s 723ms/step - loss: 0.1369 - acc: 0.9802 - val_loss: 1.1463 - val_acc: 0.6834

Epoch 00001: val_acc improved from -inf to 0.68340, saving model to /data/oxford102/experiments/1544327751.1324658/vgg19_1544327751.1324658.h5
Epoch 2/100
71/71 [==============================] - 47s 665ms/step - loss: 0.1201 - acc: 0.9859 - val_loss: 1.2191 - val_acc: 0.6985

Epoch 00002: val_acc improved from 0.68340 to 0.69853, saving model to /data/oxford102/experiments/1544327751.1324658/vgg19_1544327751.1324658.h5
Epoch 3/100
71/71 [==============================] - 47s 661ms/step - loss: 0.1182 - acc: 0.9824 - val_loss: 1.0393 - val_acc: 0.7124

Epoch 00003: val_acc improved from 0.69853 to 0.71236, saving model to /data/oxford102/experiments/1544327751.1324658/vgg19_1544327751.1324658.h5
Epoch 4/100
71/71 [==============================] - 47s 663ms/step - loss: 0.1097 - acc: 0.9832 - val_loss: 1.1543 - val_acc: 0.7096

Epoch 00004: val_acc did 